### Modelo de redes neuronales: LiftAdvisor

Con la intención de cumplir con los objetivos planteados, hemos subdividido nuestro modelo de redes neuronales general en dos partes:
1. Modelo de detección de poses: Este modelo funcionará con redes neuronales convolucionales, con el objetivo de captar las imágenes necesarias para detectar la pose de sentadilla, ya sea de frente o de lado, y devolver las coordenadas de las articulaciones de interés.
2. Modelo de clasificación y calificación de técnica: Funciona con una red neuronal común, la cual en base a ciertos criterios (que serán especificados posteriormente), recibe las coordenadas halladas en el modelo anterior, y determina la calidad de la sentadilla en un sistema de calificación del 1 al 10.

Las unidades de trabajo en la clase de Matemáticas Aplicadas II que se ven involucradas en este proyecto son:
1. Unidad 2: Vectores y matrices
2. Unidad 3: Optimización

Subdividiremos este proyecto en las siguientes partes:
1. Preprocesamiento y preparación de datos: Divideremos nuestro lote de videos en el grupo de entrenamiento y técnica. La intención es que el modelo de detección de poses devuelva tanto la lista de coordenadas de articulaciones de interés, y se haga un etiquetado automático para poder entrenar y evaluar al segundo modelo.
2. Desarrollo del modelo: Se desarrollará el modelo de clasificación y calificación, explicando a profundidad el algoritmo de forward propagation.
3. Entrenamiento del modelo: Ya que el éxito del modelo depende de su aprendizaje, plantearemos el algoritmo de backpropagation.
4. Evaluación del modelo: En base a nuestro lote de videos y haciendo uso del output del primer modelo, entrenaremos al segundo modelo para que sea capaz de calificar la técnica de una sentadilla de forma correcta.

### 1. Preprocesamiento y preparación de datos

Crearemos un modelo implementando las bibliotecas OpenCV y MediaPipe, con el objetivo de detectar la pose de sentadilla (ya sea de frente o de lado) y obtener las coordenadas de las articulaciones de interés. Posteriormente, haremos un proceso de etiquetado automático para cada criterio, y procesaremos nuestro lote de videos de modo que después pueda ser usado para el entrenamiento y evaluación del segundo modelo de redes neuronales.

pd: Recordar que la explicación matemática de este primer modelo se realizará posteriormente.

In [1]:
import cv2
import mediapipe as mp
import numpy as np
import csv
import os
import glob
import pandas as pd

#### ¿Cómo se detecta la pose de sentadilla?

Estamos interesados en guardar solo las coordenadas en los momentos en los que se esté ejecutando una sentadilla. Para reconocer cuándo esta se ejecuta, lo que haremos es calcular el ángulo de las rodillas, usando como vértices la cadera, la rodilla y el tobillo.

Debemos primeramente tomar en cuenta que en Mediapipe, al tomar las coordenadas de las articulaciones se hace de forma tridimensional, es decir, que cada keypoint tiene 3 componentes: x, y, z. De modo que no podemos calcular el ángulo entre estos tres puntos de forma común, sino que los vamos a tomar como vectores. Usaremos la fórmula:

$$\cos \theta = \frac{<x,y>}{\|x\| \|y\|}$$
$$ \theta = \arccos(\frac{<x,y>}{\|x\| \|y\|})$$

Para así aprovechar las propiedades del producto punto y hacer el cálculo sin usar mucha trigonometría.

1. Calcular vectores: Como estamos interesados en el ángulo formado en la rodilla, tomaremos dos vectores en cuenta. Si $p1$ es la cadera, $p2$ es la rodilla y $p3$ es el tobillo:
$$p_1-p_2=v_1$$
$$p_3-p_2=v_2$$
Donde ambos serían vectores con origen en $p_2$

2. Calcular producto punto: Para calcular el producto punto, se deben multiplicar cada uno de los componentes entre sí, por pares, para después sumarlos (básicamente una combinación lineal), de modo que:
$$x \cdot y = (x_1 \cdot y_1)+(x_2 \cdot y_2)+(x_3 \cdot y_3)$$

3. Calcular norma de cada vector: En numpy se maneja la norma euclidiana, donde lo que hacemos es calcular la raíz cuadrada de la suma de los elementos del vector, elevado cada uno al cuadrado:

$$\|x \| = \sqrt{(x_1)^2 + (x_2)^2 + (x_3)^2}$$
$$\|y \| = \sqrt{(y_1)^2 + (y_2)^2 + (y_3)^2}$$

4. Calculamos el coseno: Esto lo hacemos dividiendo el producto punto por el producto de las normas de ambos vectores:

$$\cos \theta = \frac{<x,y>}{\|x\| \|y\|}$$

5. Hallamos el ángulo: Lo hacemos aplicando arcocoseno, con el objetivo de despejar el ángulo final
$$ \theta = \arccos(\frac{<x,y>}{\|x\| \|y\|})$$

Ahora podemos verlo aplicado en código:

In [2]:
# Función para verificar la pose de sentadilla
def calcular_angulo(p1, p2, p3):
    v1 = p1 - p2
    v2 = p3 - p2
    dot_product = np.dot(v1, v2)
    norm_v1 = np.linalg.norm(v1)
    norm_v2 = np.linalg.norm(v2)
    cos_theta = dot_product / (norm_v1 * norm_v2)
    cos_theta = np.clip(cos_theta, -1, 1)
    angulo = np.arccos(cos_theta)
    return np.degrees(angulo)

def es_sentadilla(keypoints):
    angulo_rodilla_izquierda = calcular_angulo(keypoints[23], keypoints[25], keypoints[27])
    angulo_rodilla_derecha = calcular_angulo(keypoints[24], keypoints[26], keypoints[28])

    # Supongamos que una sentadilla se detecta si ambos ángulos de las rodillas son menores a 90 grados
    if angulo_rodilla_izquierda < 90 and angulo_rodilla_derecha < 90:
        return True
    return False

En este caso, al hallar el ángulo de cada rodilla respecto a su respectivo lado de cadera y tobillo, queremos que cuando el ángulo entre estos sea menor a 90 grados, es decir, la persona no esté parada de forma totalmente recta, entonces se empieza a contar como una sentadilla. Esto lo hacemos con el objetivo que el sistema capture una sentadilla incluso si no está siendo completada en el rango requerido (que debería ser cuando la cadera está a igual o menor altura que las rodillas).

#### Criterios de evaluación de técnica y etiquetado automático

Para evaluar la técnica de la sentadilla, se debe diferenciar si se está realizando desde una perspectiva frontal o lateral, ya que dependiendo de esto los criterios son distintos. Por ejemplo, en la vista frontal se puede evaluar la distancia entre las rodillas y pies, mientras que lateralmente es imposible hacerlo. 

Esto lo hacemos haciendo uso de la siguiente función, donde básicamente se toma en cuenta la diferencia entre los puntos de las caderas, tomando en cuenta que en el esqueleto hecho por Mediapipe, al estar de lado las caderas estarían alineadas, por lo tanto estarían a una distancia $x$ muy cercana.

In [3]:
def detectar_perspectiva_sentadilla(keypoints):
    cadera_izquierda = keypoints[23]
    cadera_derecha = keypoints[24]

    # Diferencias en las coordenadas x entre las caderas, hombros y rodillas
    diferencia_cadera_x = abs(cadera_izquierda[0] - cadera_derecha[0])

    # Umbrales para diferencias en X
    umbral_diferencia_x = 0.05  # Ajusta este valor según tus datos específicos

    # Detectar perspectiva frontal
    es_frontal = (diferencia_cadera_x > umbral_diferencia_x)

    return es_frontal



Además que, el objetivo de las siguientes funciones es hacer un **etiquetado automático** de las sentadillas. Esto es necesario ya que al entrenar nuestro segundo modelo, necesita saber cuáles son los valores reales o los valores que debe predecir, de modo que pueda aprender y autocorregirse.

De este modo, nuestros criterios son:

##### Criterios de sentadilla frontal

Tomando en cuenta que es imposible que una persona ejecute de forma perfecta una técnica por factores como la anatomía individual o su biomecánica, decidimos entonces hacer uso de umbrales. Los umbrales son valores predefinidos que se utilizan para establecer límites dentro de los cuales ciertos parámetros (en este caso los criterios) se consideran aceptables o correctos. Estos umbrales permiten cuantificar y evaluar la calidad de la postura o movimiento en términos de alineación, profundidad, estabilidad, inclinación, posición, y distribución del peso.

In [28]:
# Umbrales para los criterios de evaluación
umbral_alineacion = 0.02  # Umbral para la alineación de las rodillas
umbral_profundidad = 0.03  # Umbral para la profundidad de la sentadilla
umbral_estabilidad = 0.1  # Umbral para la estabilidad de la cadera
umbral_inclinacion = 0.01  # Umbral para la inclinación del cuerpo
umbral_rodillas = 0.1  # Umbral para la posición de las rodillas
umbral_rodillas_lateral = 0.09  # Umbral para la posición de las rodillas
umbral_peso = 10  # Umbral para la distribución del peso

1. Alineación de las rodillas: Las rodillas deben estar alineadas con los pies, no deben ceder hacia adentro ni hacia afuera durante la fase de descenso o ascenso.

Para comprobar que esto se cumpla, tomaremos la distancia entre las rodillas y los pies, y mientras la distancia entre las rodillas sea igual a la distancia de los pies (considerando un margen de error calculado con el umbral), el puntaje será máximo.

Si no es así, el puntaje se calcula tomando en cuenta la proporción entre la distancia entre las rodillas y los pies. Entre más similar sea la distancia entre ambos, el valor será más cercano a 0. Restamos el umbral de alineación para tomar en cuenta el rango de error, y multiplicamos por un factor de penalización con el objetivo de escalar el error y se vea representado de mejor manera en la calificación final. Finalmente, restamos esta ecuación del puntaje máximo, obteniendo finalmente el puntaje según el grado de error.

nota: Usamos la función max(x,y) para asegurarnos que por más bajo que sea el valor, nunca sea menor a 1.

In [29]:
def alineacion_rodillas_frontal(keypoints):
    rodilla_izquierda = keypoints[25]
    rodilla_derecha = keypoints[26]
    pie_izquierdo = keypoints[23]
    pie_derecho = keypoints[24]
    
    distancia_rodillas = abs(rodilla_izquierda[0] - rodilla_derecha[0])
    distancia_pies = abs(pie_izquierdo[0] - pie_derecho[0])
    
    puntaje_maximo = 10
    
    if distancia_rodillas == umbral_alineacion * distancia_pies:
        puntaje = puntaje_maximo
    else:
        puntaje = max(1, puntaje_maximo - 5 * (distancia_rodillas / distancia_pies - umbral_alineacion))
    
    return puntaje

2. Profundidad de sentadilla: La cadera debe descender por debajo de la parte superior de la rodilla para cumplir con los estándares de una sentadilla completa.

En este caso somos más flexibles, de modo que la cadera debe estar ya sea igual o menor altura que las rodillas, aún tomando en cuenta un umbral que permita un rango de error.

En este caso, la calificación depende de la condición anteriormente establecida, calculando la diferencia de altura en ambos lados (izquierdo y derecho), y promediando la calificación de ambos lados para obtener el puntaje final.

In [30]:
def profundidad_frontal(keypoints):
    cadera_izquierda = keypoints[23]
    rodilla_izquierda = keypoints[25]
    
    cadera_derecha = keypoints[24]
    rodilla_derecha = keypoints[26]
    
    diferencia_izquierda = rodilla_izquierda[1] - cadera_izquierda[1]
    diferencia_derecha = rodilla_derecha[1] - cadera_derecha[1]
    
    # Calificación basada en la profundidad.
    if diferencia_izquierda <= 0:
        calificacion_izquierda = 10
    else:
        calificacion_izquierda = max(1, 10 - (diferencia_izquierda / umbral_profundidad))
    
    if diferencia_derecha <= 0:
        calificacion_derecha = 10
    else:
        calificacion_derecha = max(1, 10 - (diferencia_derecha / umbral_profundidad))
    
    return (calificacion_izquierda + calificacion_derecha) / 2



3. Estabilidad de la cadera: La cadera debe permanecer estable y no rotar hacia un lado durante la ejecución de la sentadilla.

Esto simplemente se halla con la diferencia de altura entre un lado de la cadera y el otro, de modo que se mantengan a la misma altura. Se calcula la calificación como en los casos anteriores, tomando en cuenta la proporción de la desviación respecto al umbral permitido.

In [31]:
def estabilidad_cadera_frontal(keypoints):
    cadera_izquierda = keypoints[23]
    cadera_derecha = keypoints[24]
    
    desviacion_cadera = np.abs(cadera_izquierda[1] - cadera_derecha[1])
    
    # Calificación basada en la estabilidad. Cuanto menor la desviación, mayor la calificación.
    return max(1, 10 - (desviacion_cadera / umbral_estabilidad))

##### Criterios de sentadilla lateral

4. Profundidad: La cadera debe descender por debajo de la línea de la rodilla para cumplir con los estándares de una sentadilla completa.

Funciona de forma similar a la perspectiva frontal, solo que es simplificado al solo tomar una rodilla en cuenta (por estar de lado)

In [32]:
def profundidad_lateral(keypoints):
    cadera = keypoints[23]  # Suponiendo una vista lateral de la cadera
    rodilla = keypoints[25]  # Rodilla correspondiente
    
    diferencia = cadera[1] - rodilla[1]
    
    # Calificación basada en la profundidad.
    # Si la cadera está al mismo nivel o por debajo de la rodilla, la puntuación es 10.
    # Si la cadera está por encima de la rodilla, la puntuación disminuye gradualmente de 10 a 1.
    if diferencia <= 0:  # La cadera está al mismo nivel o por debajo de la rodilla
        return 10
    else:  # La cadera está por encima de la rodilla
        return max(1, 10 - (diferencia / umbral_profundidad))

5. Inclinación de la espalda: La espalda debe permanecer en una posición neutral, ni demasiado arqueada ni demasiado redondeada.

Este básicamente toma en cuenta que la persona no esté haciendo arcos innecesarios con su espalda.  En este caso, asumimos al vector espalda como la diferencia entre el hombro y la cadera. Para calcular el ángulo hacemos uso de una propiedad trigonométrica básica, donde para un triángulo rectángulo, la tangente de un ángulo $\theta$ es la razón entre el cateto opuesto $y$ y el cateto adyacente $x$ es $\tan \theta = \frac{y}{x}$
​

Entonces, para encontrar el ángulo $\theta$, usamos la función arcotangente:

$$\theta=\arctan(\frac{y}{x})$$

Y multiplicamos por $\frac{180}{\pi}$ con el objetivo de convertir el anterior cálculo (que está en radianes) a grados.

Por lo demás, continuando haciendo los cálculos como en las funciones anteriores.

In [33]:
def inclinacion_espalda_lateral(keypoints):
    hombro = keypoints[11]  # Suponiendo una vista lateral del hombro
    cadera = keypoints[23]
    
    vector_espalda = hombro - cadera
    angulo_espalda = np.arctan2(vector_espalda[1], vector_espalda[0]) * (180 / np.pi)
    
    # Calificación basada en la arqueadura de la espalda.
    # Si la espalda está recta o menos arqueada, la puntuación es 10.
    # Si la espalda está más arqueada, la puntuación disminuye gradualmente de 10 a 1.
    if angulo_espalda <= umbral_inclinacion:  # Espalda recta o menos arqueada
        return 10
    else:  # Espalda más arqueada
        return max(1, 10 - abs(angulo_espalda - umbral_inclinacion) / umbral_inclinacion)


6. Posición de las rodillas: Las rodillas deben seguir la línea de los pies, sin sobrepasar los dedos de los pies ni ceder hacia adentro.

Esto también es calculado como una diferencia, entre la rodilla y el tobillo, sacando la calificación como lo hemos hecho anteriormente.

In [34]:
def posicion_rodillas_lateral(keypoints):
    rodilla = keypoints[25]
    tobillo = keypoints[27]
    
    diferencia = rodilla[0] - tobillo[0]
    
    # Calificación basada en la posición.
    # Si la diferencia es menor o igual al umbral, la puntuación es 10. 
    # De lo contrario, se calcula la puntuación.
    if abs(diferencia) <= umbral_rodillas_lateral:
        return 10
    else:
        return max(1, 10 - (abs(diferencia) / umbral_rodillas_lateral))


7. Distribución del peso: El peso (corporal) debe estar distribuido de manera uniforme sobre los pies, sin que se desplace excesivamente hacia los talones o los dedos de los pies.

Para hallar la distribución, se calcula la distancia horizontal absoluta entre la cadera y el talón, que mide cuán desplazada está la cadera en relación con el talón, y hace lo mismo respecto a los dedos, para después hallar el mínimo entre estas dos distancias calculadas. El propósito entonces es medir cuán centrada está la cadera en relación con el pie.

In [35]:
def distribucion_peso_lateral(keypoints):
    talon = keypoints[27]
    dedos = keypoints[28]
    cadera = keypoints[23]
    
    desplazamiento_peso = min(np.abs(cadera[0] - talon[0]), np.abs(cadera[0] - dedos[0]))
    
    # Calificación basada en la distribución del peso. Cuanto menor el desplazamiento, mayor la calificación.
    return max(1, 10 - (desplazamiento_peso / umbral_peso))

#### Ejecutar modelo

Como mencionamos anteriormente, el objetivo principal de este modelo es procesar y etiquetar los datos para que puedan ser usados posteriormente por el segundo modelo. De este modo, los datos de los frame que tengan sentadilla de todos los videos serán guardados en formato csv, que serán más fáciles de implementar.

Primeramente, debemos crear la función que nos permita inicializar el csv de acuerdo a nuestras necesidades:

In [36]:
def inicializar_csv(csv_file):
    if not os.path.exists(csv_file):
        with open(csv_file, mode='w', newline='') as file:
            writer = csv.writer(file)
            headers = ['frame']
            for i in range(11, 15):
                headers.extend([f'x_{i}', f'y_{i}', f'z_{i}'])
            for i in range(23, 29):
                headers.extend([f'x_{i}', f'y_{i}', f'z_{i}'])
            headers.extend(['alineacion_rodillas_frontal', 'profundidad_frontal', 'estabilidad_cadera_frontal', 'profundidad_lateral', 'inclinacion_espalda_lateral', 'posicion_rodillas_lateral', 'distribucion_peso_lateral'])
            writer.writerow(headers)

Una característica clave, es que al detectar que la sentadilla es frontal o lateral, solo se guardan las clasificaciones respecto a esos criterios, mientras que los otros criterios (que no aplican) se quedarán en 0.

In [37]:
# Inicializar Mediapipe Pose
mp_pose = mp.solutions.pose
pose = mp_pose.Pose()
mp_drawing = mp.solutions.drawing_utils

# Función para procesar un video y detectar la pose de sentadilla
def detectar_sentadilla(video_path, csv_file):
    cap = cv2.VideoCapture(video_path)
    frame_count = 0

    if not cap.isOpened():
        print("Error: No se puede abrir el video.")
        return

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        # Convertir imagen de BGR a RGB
        image = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        image.flags.writeable = False

        # Detectar poses
        results = pose.process(image)

        # Convertir imagen de RGB a BGR
        image.flags.writeable = True
        image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)

        if results.pose_landmarks:
            keypoints = np.array([[lm.x, lm.y, lm.z] for lm in results.pose_landmarks.landmark])

            if es_sentadilla(keypoints):
                keypoints_necesarios = keypoints[[11, 12, 13, 14, 23, 24, 25, 26, 27, 28], :].flatten()
                with open(csv_file, mode='a', newline='') as file:
                    writer = csv.writer(file)
                    if detectar_perspectiva_sentadilla(keypoints):
                        resultado_alineacion = alineacion_rodillas_frontal(keypoints)
                        resultado_profundidad_frontal = profundidad_frontal(keypoints)
                        resultado_estabilidad = estabilidad_cadera_frontal(keypoints)
                        writer.writerow([frame_count] + keypoints_necesarios.tolist() + [resultado_alineacion, resultado_profundidad_frontal, resultado_estabilidad, 0, 0, 0, 0])
                        cv2.putText(image, 'Sentadilla frontal detectada', (50, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2, cv2.LINE_AA)
                    else:
                        resultado_profundidad = profundidad_lateral(keypoints)
                        resultado_inclinacion = inclinacion_espalda_lateral(keypoints)
                        resultado_posicion_rodillas = posicion_rodillas_lateral(keypoints)
                        resultado_distribucion_peso = distribucion_peso_lateral(keypoints)
                        writer.writerow([frame_count] + keypoints_necesarios.tolist() + [0, 0, 0, resultado_profundidad, resultado_inclinacion, resultado_posicion_rodillas, resultado_distribucion_peso])
                        cv2.putText(image, 'Sentadilla lateral detectada', (50, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2, cv2.LINE_AA)

            mp_drawing.draw_landmarks(image, results.pose_landmarks, mp_pose.POSE_CONNECTIONS)

        cv2.imshow('Pose Detection', image)
        frame_count += 1

        if cv2.waitKey(10) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

Con el modelo creado, lo que debemos hacer ahora es subdividir nuestros datos en datos de entrenamiento y validación, de modo que ahora los podemos procesar, etiquetar automáticamente, y tenemos finalmente los datos listos para que puedan entrenar a nuestro modelo de clasificación.

In [38]:
def procesar_videos(carpeta_base):
    # Crear las subcarpetas de entrenamiento y validación si no existen
    carpeta_training = os.path.join(carpeta_base, 'training')
    carpeta_validation = os.path.join(carpeta_base, 'validation')
    os.makedirs(carpeta_training, exist_ok=True)
    os.makedirs(carpeta_validation, exist_ok=True)

    # Inicializar los archivos CSV para cada subcarpeta
    csv_file_training = os.path.join(carpeta_training, 'squat_coordinates_training.csv')
    csv_file_validation = os.path.join(carpeta_validation, 'squat_coordinates_validation.csv')
    inicializar_csv(csv_file_training)
    inicializar_csv(csv_file_validation)

    # Obtener todos los videos en la carpeta base
    video_paths = glob.glob(os.path.join(carpeta_base, '*.mp4'))

    # Dividir los videos en entrenamiento y validación
    num_videos = len(video_paths)
    num_training = int(num_videos * 0.8)
    training_videos = video_paths[:num_training]
    validation_videos = video_paths[num_training:]

    # Procesar los videos de entrenamiento
    for video_path in training_videos:
        if os.path.exists(video_path):
            detectar_sentadilla(video_path, csv_file_training)
        else:
            print(f"El archivo {video_path} no existe.")

    # Procesar los videos de validación
    for video_path in validation_videos:
        if os.path.exists(video_path):
            detectar_sentadilla(video_path, csv_file_validation)
        else:
            print(f"El archivo {video_path} no existe.")

# Utilizar la función para procesar los videos en la carpeta 'squat_data'
carpeta_base = 'squat_data'
procesar_videos(carpeta_base)

C:\Users\KAROLD\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\google\protobuf\symbol_database.py:55: UserWarning: SymbolDatabase.GetPrototype() is deprecated. Please use message_factory.GetMessageClass() instead. SymbolDatabase.GetPrototype() will be removed soon.
  warnings.warn('SymbolDatabase.GetPrototype() is deprecated. Please '


KeyboardInterrupt: 

Al finalizar esta función, tenemos en nuestra carpeta *squat_data* dos subcarpetas, cada con un csv que contiene la información de los datos con su respectivo etiquetado automático.

### 2. Desarrollo del segundo modelo: Forward propagation

Como especificamos anteriormente, el objetivo de nuestro segundo modelo es la calificación de los criterios de la pose sentadilla. Para ello, haremos uso de una red neuronal.

En sí, una red neuronal trabaja como una gran función (compuesta por otras funciones más pequeñas), la cual se construye y se va dando forma a través de la constante modificación de sus parámetros, con la intención de perfeccionar los resultados y que sean lo más exactos y precisos posibles.

En esta sección, nos enfocaremos en la primera parte: Construir la "gran función", mejor conocido como *forward propagation*. Pero antes, entendamos la estructura de una red neuronal

#### Estructura de la red neuronal

Debemos saber que, lo que hace una red neuronal generalmente es tomar una serie de atributos/datos como input, y devolver lo que suele ser una predicción o clasificación, dependiendo de lo que quiera que haga la red.

Una red está compuesta de **neuronas**, que en palabras simples lo podemos ver como un algo que contiene un número. Este número lo podemos llamar **activación**. Si tenemos un ejemplo de entrenamiento, llamémoslo dato, y este cuenta con unos atributos específicos, cada atributo puede ser reconocido como una neurona. Así, la totalidad de los atributos del dato, conformarán **la primera capa de la red**.

Como describimos anteriormente, en general las capas de una red están, igualmente conformadas por neuronas. Existen tres tipos de capas:
1. Capa de entrada: La descrita anteriormente, es la primera capa de la red que recibe los atributos de entrada.
2. Capas ocultas: Estas capas son útiles para transformar y extraer las características más importantes de la información recibida.
3. Capa de salida: Es la última capa de la red que produce la predicción final, el cual lo devuelve en el formato requerido.

**¿Cómo pasamos la información de capa en capa?**

Cada neurona en cada capa (posterior a la primera) está conectada a todas las neuronas de la capa anterior. Esta está "conectada" por medio de unos coeficientes llamados **pesos**, que su tarea es básicamente determinar qué tanta influencia/impacto tiene una activación/neurona/resultado en la capa anterior respecto al cálculo en la nueva neurona. Además de incluir un bias, que es un parámetro adicional que permite a la red ajustar su comportamiento y mejorar su capacidad de aprendizaje.

Primero definamos la notación que veremos más adelante:

In [ ]:
from IPython.display import display, HTML

img1 = "img_redesNeuronales/neuronaNotacion.png"
img2 = "img_redesNeuronales/pesoNotacion.png"
img3 = "img_redesNeuronales/biasNotacion.png"

html = f"""
<div style="display: flex; justify-content: space-around;">
    <div style="flex: 1; text-align: center;">
        <img src="{img1}" style="max-width: 100%; height: auto;" />
    </div>
    <div style="flex: 1; text-align: center;">
        <img src="{img2}" style="max-width: 100%; height: auto;" />
    </div>
    <div style="flex: 1; text-align: center;">
        <img src="{img3}" style="max-width: 100%; height: auto;" />
    </div>
</div>
"""

display(HTML(html))


Entonces, podemos observar de manera gráfica aquella relación en esta pequeña red neuronal de este modo:

In [ ]:
from IPython.display import display, Image

ruta_imagen = "img_redesNeuronales/miniRed1.png"
display(Image(filename=ruta_imagen, width=500))

Donde los pesos se ubican en este lugar

In [ ]:
from IPython.display import display, Image

ruta_imagen = "img_redesNeuronales/miniRed2.png"
display(Image(filename=ruta_imagen, width=500))

Continuando con el ejemplo anterior, matemáticamente hablando, estamos tratando con una **combinación lineal**, donde los pesos representarían los coeficientes y los resultados de las neuronas serían las variables:

$$z=w_{0,0}a_0^{(0)}+w_{0,1}a_1^{(0)}+w_{0,2}a_2^{(0)} + b_0$$

Pero la neurona no solo recibe esto, ya que si fuese así, una red neuronal no sería más que combinaciones lineales, lo que no permitiría captar las particularidades de los datos y generar buenas predicciones. Para añadir no linealidad, usamos **funciones de activación**. Hay múltiples, pero en nuestro caso usaremos la función ReLU y la función sigmoide. La función ReLU, en pocas palabras, hace que cualquier valor negativo sea $0$ (convirtiendo a la neurona en una neurona muerta y haciendo que ya no contribuya más) y los valores positivos se queden igual.

$$ReLU(z)=max(0,z)$$

Mientras que la sigmoide es una función con una curva característica en forma de "S" o curva sigmoide que transforma cualquier valor en el dominio $(-\infty,\infty)$ en un número entre $0$ y $1$:



Entonces, finalmente la información que recibiría nuestra neurona en nuestro pequeño ejemplo es:

$$a_0^{(1)}=\sigma(z)$$


Si tuviéramos entonces una capa inicial con 3 neuronas, y una capa intermedia también con 3:

In [ ]:
from IPython.display import display, Image

ruta_imagen = "img_redesNeuronales/miniRed3.png"
display(Image(filename=ruta_imagen, width=500))

Como calcular neurona por neurona consumiría mucho tiempo y espacio, lo que hacemos es implementar el álgebra matricial para representar toda una capa de neuronas. Los pesos los representaremos en una matriz, y las activaciones de la capa actual serán un vector vertical:

$$\begin{pmatrix}w_{0,0}&w_{0,1}&w_{0,2}\\ w_{1,0}&w_{1,1}&w_{1,2}\\ w_{2,0}&w_{2,1}&w_{2,2}\end{pmatrix} \begin{pmatrix}a_0^{\left(0\right)}\\ \:a_1^{\left(0\right)}\\ \:a_2^{\left(0\right)}\end{pmatrix}=\begin{pmatrix}?\\ ?\\ \:?\end{pmatrix}$$

Cada fila representa los pesos para cada neurona en la nueva capa. Al multiplicar la matriz de pesos por la matriz de activaciones de la capa actual, el resultado es un vector que contiene las neuronas sin aplicar el bias ni la función de activación. De este modo, la ecuación completa sería:

$$a^{(1)}=\sigma(\begin{pmatrix}w_{0,0}&w_{0,1}&w_{0,2}\\ w_{1,0}&w_{1,1}&w_{1,2}\\ w_{2,0}&w_{2,1}&w_{2,2}\end{pmatrix} \begin{pmatrix}a_0^{\left(0\right)}\\ \:a_1^{\left(0\right)}\\ \:a_2^{\left(0\right)}\end{pmatrix})+\begin{pmatrix}b_0\\ b_1\\ b_2\end{pmatrix}$$

Que en forma de función lo podemos ver como:

$$a^{(1)}=\sigma(W a_0 + b)$$

Donde $W$ es la matriz de pesos, $a_0$ es el vector de activaciones de la capa actual y $b$ es el bias o sesgo. No olvidemos también que $z=W a_0 + b$, que será útil recordarlo para futuros cálculos.

Así que finalmente, calculamos la capa entera, lo que nos ahorrará tiempo a la hora de codificar. Y como podemos ver, *la salida de cada capa será usada como entrada de la próxima.*

#### Planteamiento de nuestra propia red neuronal

Con lo anterior ya explicado, podemos construir entonces la red neuronal que usaremos como modelo de calificación de sentadilla.

En este caso, construiremos un modelo con una totalidad de 3 capas: 1 capa de entrada, 1 capa oculta y 1 capa de salida.

* Capa de entrada: Como estamos interesados en 10 articulaciones, y cada articulación tiene 3 coordenadas $(x, y, z)$, la capa de entrada recibirá 30 datos, por lo que tendrá 30 neuronas.
* Capa oculta: Comenzaremos con una capa de 6 neuronas. Es solo una capa oculta con una cantidad tan pequeña de neuronas ya que debido al tamaño de la muestra de datos, es la mejor manera de evitar el sobreajuste y poder captar los patrones en la información.
* Capa de salida: Tiene 7 neuronas, que son los 7 criterios a calificar por sentadilla. Como queremos que produzca resultados del 1 al 10, en esta capa usaremos la función sigmoide.

#### Algoritmo de forward propagation

En primera instancia, los pesos son elegidos de forma aleatoria, ya que en el siguiente proceso, backpropagation, la red irá aprendiendo y modificando estos parámetros. Entonces procederemos a inicializarlos:

In [4]:
def init_params(layer_sizes):
    weights = []
    biases = []
    for i in range(len(layer_sizes) - 1):
        w = np.random.randn(layer_sizes[i], layer_sizes[i + 1]) * 0.01
        b = np.zeros((1, layer_sizes[i + 1]))
        weights.append(w)
        biases.append(b)
    return weights, biases

Obtenemos un código que al ingresar un arreglo que especifica la cantidad de neuronas por entrada, y nos devuelve dos listas de matrices: weights y biases, donde cada matriz de la primera lista representa los pesos de una capa de la red neuronal, y la segunda representa los sesgos de una capa de la red neuronal.

El siguiente paso es definir nuestras funciones de activación, que en este caso usaremos $\sigma$ y $ReLU$:

In [5]:
# Función Sigmoide
def sigmoide(x):
    return 1 / (1 + np.exp(-x))

# Función ReLU
def relu(x):
    return np.maximum(0, x)

Con nuestras funciones listas, procedemos a plantear nuestra función de forward propagation, que funcionará de manera sequencial, como fue planteada en el punto anterior:

In [6]:
def forward_propagation(X, pesos, bias):
    activaciones = [X]
    z = []

    a = X
    for l in range(len(pesos)):
        z_l = np.dot(a, pesos[l]) + bias[l]
        z.append(z_l)
        a = sigmoide(z_l)
        activaciones.append(a)

    return activaciones, z

Con esto podemos dar por terminado la primera parte del algoritmo, que es "alimentarlo" con la información. En el siguiente punto, haremos el proceso de calcular el error y corregir para cumplir el objetivo de aprendizaje.


### 3. Entrenamiento del modelo: Backward propagation

El propósito final del machine learning, como su nombre lo indica, es aprender, ya que la práctica es la única forma de refinar sus parámetros y así lograr hacer predicciones y en este caso, clasificaciones correctas.

En esta sección, construiremos el algoritmo que se encarga de calcular el error y hacer las correcciones debidas para lograr el objetivo del aprendizaje de máquinas.

#### ¿Cómo funciona?

Para explicarlo, retomaremos nuestra última pequeña red compuesta por 3 neuronas en la capa inicial, 3 neuronas en la capa intermedia y una neurona en la capa de salida. En lo que quedamos en el algoritmo de *forward propagation* fue en la última capa, donde finalmente obtuvimos unas predicciones basadas (inicialmente) en pesos y sesgos random. Como es de esperarse, obtendremos una mala predicción, pero ¿El modelo cómo sabe que se está equivocando o cuánto se está equivocando?

**Función de error o pérdida o costo**

Al llegar a la capa de salida y obtener nuestros resultados, para saber qué tan bien lo hizo el modelo lo que hacemos es compararlo con los valores reales que debió haber obtenido en ese ejemplo de entrenamiento y para esa salida específica (por eso es necesario el etiquetado del material de entrenamiento y validación). Aunque usualmente, la función de costo se ve así:

$$C=(y-a^L)^2$$

Que sería el cuadrado de esa diferencia entre $y$ que representa el valor real y la salida. Esta diferencia lo que nos dice es cuán equivocada está la precisión respecto al valor, así que mientras más cercano sea a 0, es porque nuestra predicción es más correcta.

*Recordemos que si queremos que la predicción en una neurona cambie, solo tenemos 3 opciones: Modificar los pesos, modificar el bias o modificar las activaciones de la capa anterior a la de la neurona. Por esta relación intrínseca es que debemos realizar backpropagation, ya que con el fin de mejorar el resultado final, se deben cambiar de forma consecutiva, de atrás para adelante (para saber cuánto cambiar en función al error) los parámetros, para que se ajusten a los valores reales.*

**¿Cómo aprende el modelo?**

Entonces, si nuestro modelo ya sabe qué tan equivocado está, ¿Cómo podemos usar esta información para mejorar el modelo? Podemos calcular entonces cómo el cambio en alguna de nuestras neuronas afecta el resultado en el costo, lo que sería calcular la derivada del costo respecto a las activaciones. Queremos saber esto ya que nos dice cómo cambiar el valor de cada predicción para minimizar el costo, y como mencionamos anteriormente, entre más cercano sea el costo a $0$ es porque nuestra predicción es más acertada.



**Calcular el error de la última capa**

De este modo, si queremos hallar cómo el cambio en estos valores modificables (pesos, bias y activaciones) afecta al costo, lo podemos definir como:

$$\delta^{(L)}=\frac{\partial C}{\partial z^L}$$

Pero, como no podemos calcular esta derivada de forma directa, podemos descomponerla a modo de regla de la cadena:

$$\delta^{(L)}=\frac{\partial C}{\partial a^L} \frac{\partial a^L}{\partial z^L}$$

Que entonces, describe cómo el costo se ve afectado por las activaciones, y cómo las activaciones se ven afectadas por sus respectivos $z$. Recordemos que $z^l$ es un vector donde cada elemento es el $z$ de cada de neurona.

Entonces, podemos hallar cada una de estas derivadas:

* Si la función de costo es la definida con anterioridad, tenemos que su derivada sería $\frac{\partial C}{\partial a^L}=2(a^L-y)$
* Mientras que $\frac{\partial a^L}{\partial z^L}=\sigma'(z^L)$

Finalmente, tenemos que la fórmula para calcular el error de la última capa es:

$$\delta^{(L)}=2(a^L-y) \sigma'(z^L)$$

**Calcular el error de cualquier capa**

Para aplicar cambios en cualquier capa que no sea la primera, es necesario ajustar los parámetros de la capa anterior, ya que, como sabemos, la salida actual de una capa depende directamente de los resultados que esta entrega. Por lo tanto, el error obtenido en la capa actual proporciona retroalimentación a la capa anterior. Al mostrar cómo fue afectada por sus resultados, esta retroalimentación ayuda a determinar cuánto deben ajustarse los parámetros de la capa anterior para contribuir a la reducción del error.

Si seguimos la lógica anterior, donde queríamos saber cómo los parámetros y variables de la capa actual afectaban a la función de costo, sería casi como construir una regla de la cadena en reversa, ya que:

$$\frac{\partial C}{\partial z^l}=\frac{\partial a^l}{\partial z^l} \frac{\partial z^{l+1}}{\partial a^l} \frac{\partial C}{\partial z^{l+1}}$$

Como mencionamos anteriormente, para saber cómo el costo se ve afectado por la capa actual (que no es de salida), debemos reconocer cómo impactó a la capa siguiente a ella, y cómo este impacto se relaciona con las variables y parámetros de la capa actual. Esta derivada también la podemos simplificar al ponerla de esta forma, donde:

* $\frac{\partial a^l}{\partial z^l}$: Reconocemos esto desde la función anterior, y sabemos que su derivada es $\sigma'(z^l)$
* $\frac{\partial z^{l+1}}{\partial a^l}$: Para hallar esta derivada, recordemos la relación entre ambas variables que es $z^{l+1} = W^{l+1} \cdot a^l + b^{l+1}$, donde al derivar ambos lados de la ecuación, obtenemos finalmente que $\frac{\partial z^{l+1}}{\partial a^l} = (W^{l+1})^T$
* $\frac{\partial C}{\partial z^{l+1}}$: Esto también loc alcuolamos con anterioridad, y lo podemos dejar como $\delta^{(l+1)}$

Finalmente, tenemos que la función para calcular el error de cualquier capa es:

$$\delta^{(l)}=[(W^{l+1})^T \delta^{(l+1)}] \odot \sigma'(z^L)$$

**Calcular el impacto de cualquier parámetro al costo**

Hemos estado mencionando que lo que nos interesa es modificar los parámetros, pero para modificarlos necesitamos saber cómo deberían ser modificados de modo que ayuden a que se reduzca la función de costo. Para saber cuánto cambiarlos, debemos hallar cómo afecta cada parámetro al costo.

Empezaremos nuevamente de forma intuitiva, planteando entonces la derivada, que la simplificaremos nuevamente en una regla de la cadena, para así poder hallar los valores más fácilmente:

$$\frac{\partial C}{\partial w_{j,k}^l}=\frac{\partial z_{j}^l}{\partial w_{j,k}^l} \frac{\partial C}{\partial z_{j}^l}$$

* Tenemos ya $\frac{\partial C}{\partial z_{j}^l}$ esta expresión identificada, que sería equivalente a $\delta_{j}^{(l)}$
* $\frac{\partial z_{j}^l}{\partial w_{j,k}^l}$: Recordemos que los pesos son parte de $z$, donde están como coeficientes de la combinación lineal. Si tenemos por ejemplo la siguiente red con los siguientes pesos:


Si queremos derivar a $z_{j}$ respecto a $w$, recordemos que:

$$z_{j}=(aw_1 + bw_2 + cw_3 + kw + b)$$

Entonces al derivar, todos los números que no involucren a $w$ quedarán en $0$, y al derivar la expresión que si lo involucre, solo quedará la activación relacionada a este peso, de modo que:

$$\frac{\partial z_{j}}{\partial w}=k$$

Donde finalmente podemos concluir que la fórmula para hallar cualquier peso es:

$$\frac{\partial C}{\partial w_{j,k}^l}=a_{k}^{l-1} \delta_{j}^{(l)}$$

Pasa una situación similar al hallar la derivada de cualquier bias. Si tenemos:

$$\frac{\partial C}{\partial b^l}=\frac{\partial z_{j}^l}{\partial b^l} \frac{\partial C}{\partial z_{j}^l}$$

Al derivar $\frac{\partial z_{j}^l}{\partial b^l}$ retomando el ejemplo anterior, todo lo que no incluya $b$ será $0$, y como $b$ no está acompañado por ningún coeficiente, entonces la derivada será $1$. El resultado final entonces sería:

$$\frac{\partial C}{\partial b^l}=\delta_{j}^{(l)}$$

**Corrección de parámetros**

Con las 4 ecuaciones anteriores, ya somos capaces de obtener el impacto de cada parámetro respecto al costo, implementando el algoritmo de backpropagation. ¿Qué hacemos entonces con toda esta información?

Como hablamos anteriormente, el objetivo es minimizar la función de costo, por lo tanto lo que haremos es aplicar un algoritmo de optimización llamado *descenso del gradiente*. Tomando en cuenta que la derivada tiende a decirnos hacia dónde crece más la función, lo que hace este algoritmo es ir exactamente al lado contrario, con la intención de hallar un mínimo local. Es un algoritmo recursivo, de modo que es ejecutado hasta hallar el mínimo de la función.

En este caso, el vector que será optimizado será el conjunto de todas las derivadas de costo respecto a parámetros (que pueden ser organizados de forma vertical a modo de vector). Lo que hace este algoritmo, es básicamente ajustar los parámetros en la dirección opuesta al gradiente, en base a una *tasa de aprendizaje* que funciona como factor de proporción para medir cuánto se le corregirá al parámetro.

La fórmula se ve:

$$\theta := \theta - \alpha \nabla C(\theta)$$

Que matricialmente hablando, lo que estamos haciendo es:

$$\theta=\begin{pmatrix}w_1-\alpha \frac{\partial C}{\partial w_1}\\ w_2-\alpha \:\frac{\partial C}{\partial w_2}\\ ...\\ w_n-\alpha \:\:\frac{\partial \:C}{\partial \:w_n}\end{pmatrix}$$

#### Algoritmo de backpropagation

Procederemos a hacer el código correspondiente, aplicando los conocimientos aprendidos. Primeramente definimos las derivadas de nuestras funciones de activación.

In [7]:
def derivada_sigmoid(x):
    s = sigmoide(x)
    return s * (1 - s)

def derivada_relu(x):
    return np.where(x > 0, 1, 0)

In [8]:
def funcion_costo(y, a_L):

    costos = (y - a_L) ** 2
    return costos

Ahora sí, implementamos el algoritmo de backpropagation, donde tomamos en cuenta $x$ que son las entradas a la primera capa, $y$ que son los valores reales respecto a las predicciones, las activaciones y sus respectivos $z$ que son resultado de la forward propagation y finalmente la tasa de aprendizaje definida a la hora de corregir los parámetros.

También dentro de esta función tenemos el algoritmo de descenso del gradiente, donde se actualizan los pesos y sesgos utilizando la regla de actualización del descenso del gradiente. La actualización se realiza para cada capa de la red neuronal, donde los pesos y sesgos se ajustan en la dirección opuesta al gradiente de la función de costo, multiplicado por la tasa de aprendizaje.

In [9]:
def backpropagation(X, y, pesos, bias, activaciones, z, tasa_aprendizaje):
    m = X.shape[0]  # Número de ejemplos de entrenamiento
    L = len(pesos)  # Número de capas
    
    # Inicializar gradientes para pesos y bias
    gradientes_pesos = [np.zeros_like(w) for w in pesos]
    gradientes_bias = [np.zeros_like(b) for b in bias]

    # Calcular el error de la última capa
    delta = (activaciones[-1] - y) * derivada_sigmoid(z[-1])
    
    # Calcular gradientes de pesos y bias para la última capa
    gradientes_pesos[-1] = np.dot(activaciones[-2].T, delta) / m
    gradientes_bias[-1] = np.sum(delta, axis=0, keepdims=True) / m

    # Backpropagate el error a capas anteriores
    for l in range(L-2, -1, -1):
        delta = np.dot(delta, pesos[l+1].T) * derivada_sigmoid(z[l])
        gradientes_pesos[l] = np.dot(activaciones[l].T, delta) / m
        gradientes_bias[l] = np.sum(delta, axis=0, keepdims=True) / m

    # Actualizar pesos y bias
    for l in range(L):
        pesos[l] -= tasa_aprendizaje * gradientes_pesos[l]
        bias[l] -= tasa_aprendizaje * gradientes_bias[l]

    return pesos, bias


### Evaluación del modelo

Con la intención de usar nuestro modelo posteriormente, creamos una función que nos permita guardar los parámetros hallados a lo largo del entrenamiento del modelo.

In [10]:
def guardar_modelo(pesos, sesgos, nombre_archivo):
    np.savez(
        nombre_archivo, 
        **{'pesos_' + str(i): pesos[i] for i in range(len(pesos))}, 
        **{'sesgos_' + str(i): sesgos[i] for i in range(len(sesgos))}
    )
    print("Modelo guardado correctamente en", nombre_archivo)

Implementamos una función de entrenamiento, donde básicamente recorre todos los entrenamientos por épocas, es decir, durante una época, el modelo ve cada ejemplo de entrenamiento una vez y ajusta sus parámetros en función de estos ejemplos para aprender de ellos. De este modo toma cada dato con sus respectivos valores reales, e implementa el algoritmo de forward propagation y de backpropagation. Esto lo hace para todos los ejemplos de entrenamiento, para finalmente guardar el modelo.

In [11]:
def train(X, y, layer_sizes, epochs, learning_rate):
    pesos, bias = init_params(layer_sizes)
    for epoch in range(epochs):
        # Iterar sobre cada ejemplo de entrenamiento
        for i in range(len(X)):
            # Obtener el ejemplo de entrenamiento actual
            ejemplo_x = X[i]
            ejemplo_y = y[i] / 10
                        
            # Forward propagation
            activaciones, z = forward_propagation(np.array([ejemplo_x]), pesos, bias)
            pesos, bias = backpropagation(ejemplo_x, ejemplo_y, pesos, bias, activaciones, z, learning_rate)

            # Imprimir la predicción final
            print("Predicción final para el ejemplo", i+1, ":", activaciones[-1][0])
            
    # Guardar el modelo después de finalizar el entrenamiento
    guardar_modelo(pesos, bias, "modelodos_entrenado.npz")
    
    return pesos, bias


In [12]:
def predecir_nuevos_datos(X_nuevos, pesos, sesgos):
    activaciones, _ = forward_propagation(X_nuevos, pesos, sesgos)
    # La predicción es la última capa de activaciones
    predicciones = activaciones[-1]
    return predicciones

In [13]:
def train_with_early_stopping(X, y, layer_sizes, epochs, learning_rate, validation_split=0.2, patience=10):
    # Inicializar los parámetros del modelo
    pesos, bias = init_params(layer_sizes)
    
    # Separar los datos en conjuntos de entrenamiento y validación
    num_examples = len(X)
    num_train = int(num_examples * (1 - validation_split))
    X_train, y_train = X[:num_train], y[:num_train]
    X_val, y_val = X[num_train:], y[num_train:]
    
    # Variables para el seguimiento de la mejor pérdida en el conjunto de validación
    best_val_loss = float('inf')
    epochs_without_improvement = 0
    
    for epoch in range(epochs):
        # Iterar sobre cada ejemplo de entrenamiento
        for i in range(len(X_train)):
            # Obtener el ejemplo de entrenamiento actual
            ejemplo_x = X_train[i]
            ejemplo_y = y_train[i] / 10
                        
            # Forward propagation
            activaciones, z = forward_propagation(np.array([ejemplo_x]), pesos, bias)
            
            # Backpropagation
            pesos, bias = backpropagation(ejemplo_x, ejemplo_y, pesos, bias, activaciones, z, learning_rate)
        
        # Calcular la pérdida en el conjunto de entrenamiento y validación
        train_loss = funcion_costo(y_train, predecir_nuevos_datos(X_train, pesos, bias))
        val_loss = funcion_costo(y_val, predecir_nuevos_datos(X_val, pesos, bias))
        
        # Imprimir la pérdida en cada época
        print(f'Epoch {epoch + 1}/{epochs} - Training Loss: {train_loss}, Validation Loss: {val_loss}')
        
        # Calcular la pérdida media en el conjunto de validación
        val_loss_mean = np.mean(val_loss)

        # Verificar si la pérdida en el conjunto de validación ha mejorado
        if val_loss_mean < best_val_loss:
            best_val_loss = val_loss_mean
            epochs_without_improvement = 0
        else:
            epochs_without_improvement += 1
            
        # Detener el entrenamiento si no hay mejora durante el número de épocas especificado
        if epochs_without_improvement >= patience:
            print(f'Early stopping at epoch {epoch + 1} due to no improvement in validation loss.')
            break
    
    # Guardar el modelo después de finalizar el entrenamiento
    guardar_modelo(pesos, bias, "modelodos_entrenado.npz")
    
    return pesos, bias

Iniciamos nuestro entrenamiento con nuestro lote de prueba.

In [14]:
# Cargar datos desde el archivo CSV
data = pd.read_csv('squat_data/training/squat_coordinates_training.csv')

# Dividir los datos en X e y
X_train = data.iloc[:, 1:31].values  # Las columnas de la 1 a la 30 son X
y_train = data.iloc[:, 31:].values   # Las columnas de la 31 en adelante son y

# Define los parámetros del modelo y del entrenamiento
layer_sizes = [30, 5, 7]
epochs = 1000
learning_rate = 0.1

# Llama a la función de entrenamiento con detención temprana
trained_weights, trained_bias = train_with_early_stopping(X_train, y_train, layer_sizes, epochs, learning_rate)


Epoch 1/1000 - Training Loss: [[3.82721620e-02 4.80263439e-01 6.87168838e-01 ... 9.66735007e+01
  9.69094072e+01 9.65375024e+01]
 [4.39838343e-02 4.64869866e-01 6.63481122e-01 ... 9.63914406e+01
  9.66290375e+01 9.63431372e+01]
 [4.38000311e-02 4.65339252e-01 6.64218327e-01 ... 9.64002155e+01
  9.66378171e+01 9.63617134e+01]
 ...
 [6.32682500e-01 3.57713405e+01 8.42258462e+01 ... 3.12632633e-02
  2.71447128e-02 3.12542582e-02]
 [6.32706229e-01 3.57892934e+01 8.42191275e+01 ... 3.12578703e-02
  2.71397211e-02 3.12488086e-02]
 [6.32779049e-01 3.57957185e+01 8.41984778e+01 ... 3.12413393e-02
  2.71244141e-02 3.12320889e-02]], Validation Loss: [[6.32775621e-01 3.57834902e+01 8.41802896e+01 ... 3.12421151e-02
  2.71251300e-02 3.12328700e-02]
 [6.32838778e-01 3.57754782e+01 8.41600695e+01 ... 3.12277857e-02
  2.71118668e-02 3.12183681e-02]
 [6.32851175e-01 3.57517952e+01 8.41382707e+01 ... 3.12249641e-02
  2.71092621e-02 3.12155216e-02]
 ...
 [3.82721620e-02 4.80263439e-01 6.87168838e-01 ...

KeyboardInterrupt: 

Con el objetivo de analizar qué tan bien se están prediciendo los datos, decidimos implementar un algoritmo de precisión, el cual nos dice del total de predicciones, cuántas fueron correctas.

In [15]:
def calcular_precision(X, y, pesos, bias, tolerancia):
    # Número de ejemplos
    m = len(X)
    
    # Inicializar contador de predicciones correctas
    predicciones_correctas = 0
    
    # Iterar sobre cada ejemplo
    for i in range(m):
        # Obtener ejemplo actual
        ejemplo_x = X[i]
        ejemplo_y = y[i] / 10
        
        # Forward propagation para hacer una predicción
        activaciones, _ = forward_propagation(np.array([ejemplo_x]), pesos, bias)
        
        # Obtener la salida predicha
        prediccion = activaciones[-1][0]  # Escalar la salida a su rango original
        
        # Comparar la predicción con la etiqueta real
        if np.allclose(prediccion, ejemplo_y, atol=tolerancia):
            predicciones_correctas += 1
    
    # Calcular la precisión
    precision = predicciones_correctas / m
    
    return precision

Como estamos tratando con números decimales altamente variados, decidimos poner un margen de tolerancia en los cuales se considerará como una aproximación aceptable, para así poder calcular la cantidad de predicciones verdaderas que tenemos.

In [16]:
# Calcular precisión
tolerancia = 0.5  # Definir una tolerancia de ±0.1
precision = calcular_precision(X_train, y_train, trained_weights, trained_bias, tolerancia)
print("Precisión del modelo en los datos de entrenamiento:", precision*100)


NameError: name 'trained_weights' is not defined

Con una tolerancia del $0.5$, tenemos una precisión de aproximadamente un $85\%&, lo cual es aceptable teniendo en cuenta la poca cantidad de datos de entrenamiento y el pequeño tamaño de la red.

### Funcionamiento del modelo

In [17]:
def cargar_modelo(nombre_archivo):
    modelo = np.load(nombre_archivo)
    pesos = [modelo['pesos_'+str(i)] for i in range(len([key for key in modelo.keys() if key.startswith('pesos_')]))]
    sesgos = [modelo['sesgos_'+str(i)] for i in range(len([key for key in modelo.keys() if key.startswith('sesgos_')]))]
    return pesos, sesgos

In [18]:
mp_pose = mp.solutions.pose
pose = mp_pose.Pose()
mp_drawing = mp.solutions.drawing_utils

def detectar_sentadilla_realtime(pesos, sesgos):
    cap = cv2.VideoCapture(0)
    frame_count = 0

    if not cap.isOpened():
        print("Error: No se puede abrir la cámara.")
        return

    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        image = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        image.flags.writeable = False

        results = pose.process(image)

        image.flags.writeable = True
        image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)

        if results.pose_landmarks:
            keypoints = np.array([[lm.x, lm.y, lm.z] for lm in results.pose_landmarks.landmark])
            if es_sentadilla(keypoints):
                keypoints_necesarios = keypoints[[11, 12, 13, 14, 23, 24, 25, 26, 27, 28], :].flatten()

                prediccion = predecir_nuevos_datos(keypoints_necesarios.reshape(1, -1), pesos, sesgos)[0]

                if detectar_perspectiva_sentadilla(keypoints):
                    cv2.putText(image, f'Alineacion Rodillas: {prediccion[0] * 10:.2f}', (10, 30), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)
                    cv2.putText(image, f'Profundidad Frontal: {prediccion[1] * 10:.2f}', (10, 60), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)
                    cv2.putText(image, f'Estabilidad Cadera: {prediccion[2] * 10:.2f}', (10, 90), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)
                elif not detectar_perspectiva_sentadilla(keypoints):
                    cv2.putText(image, f'Profundidad Lateral: {prediccion[3] * 10:.2f}', (10, 30), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)
                    cv2.putText(image, f'Inclinacion Espalda: {prediccion[4] * 10:.2f}', (10, 60), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)
                    cv2.putText(image, f'Posicion Rodillas: {prediccion[5] * 10:.2f}', (10, 90), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)
                    cv2.putText(image, f'Distribucion Peso: {prediccion[6] * 10:.2f}', (10, 120), cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2, cv2.LINE_AA)

                cv2.putText(image, 'Sentadilla detectada', (50, 250), cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2, cv2.LINE_AA)


        cv2.imshow('Pose Detection', image)
        frame_count += 1

        if cv2.waitKey(10) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

In [19]:
# Cargar el modelo guardado
pesos_cargados, sesgos_cargados = cargar_modelo("modelodos_entrenado.npz")

# Detectar sentadillas en tiempo real usando la cámara
detectar_sentadilla_realtime(pesos_cargados, sesgos_cargados)

C:\Users\KAROLD\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\google\protobuf\symbol_database.py:55: UserWarning: SymbolDatabase.GetPrototype() is deprecated. Please use message_factory.GetMessageClass() instead. SymbolDatabase.GetPrototype() will be removed soon.
  warnings.warn('SymbolDatabase.GetPrototype() is deprecated. Please '
